In [ ]:
# Install ImageMagick and dependencies
!apt-get update
!apt-get install -y imagemagick

# Modify ImageMagick policy to allow execution
!sed -i '/<policy domain="path" rights="none" pattern="@\*"/d' /etc/ImageMagick-6/policy.xml

# Install moviepy
!pip install moviepy

from moviepy.editor import VideoFileClip, ImageClip, TextClip, CompositeVideoClip
import moviepy.config as mp_config
import os

# Configure moviepy to use ImageMagick binary
mp_config.IMAGEMAGICK_BINARY = '/usr/bin/convert'

# Function to create a pixelated title clip from the first frame
def create_title_clip(input_file, output_file, title_text, duration=3.0, pixelation_factor=0.1):
    # Check if input file exists
    if not os.path.exists(input_file):
        print(f"Error: Input file {input_file} not found. Skipping.")
        return
    try:
        # Load only the first frame to minimize memory usage
        clip = VideoFileClip(input_file)
        first_frame = clip.get_frame(0)  # Get the first frame as a numpy array
        clip.close()  # Close immediately to free memory

        # Create a 3-second clip from the first frame
        frozen_clip = ImageClip(first_frame, duration=duration)

        # Apply pixelation effect to simulate blur (reduce resolution and upscale)
        from moviepy.video.fx.all import resize
        pixelated_clip = frozen_clip.fx(resize, pixelation_factor).fx(resize, 1.0 / pixelation_factor)

        # Create text clip for the title with yellow bold text
        text_clip = TextClip(
            title_text,
            fontsize=28,  # Kept for wrapping
            color='yellow',  # Simple yellow color
            font='Arial-Bold',  # Bold font
            size=(1200, 800),  # Narrower width for wrapping
            method='caption',  # Wrap text automatically
            align='center'  # Center-align text
        ).set_position('center').set_duration(duration)

        # Composite the pixelated clip and text
        final_clip = CompositeVideoClip([pixelated_clip, text_clip])

        # Save the title clip
        final_clip.write_videofile(output_file, codec='libx264', audio=False, fps=24)
        final_clip.close()
        print(f"Created title clip: {output_file}")
    except Exception as e:
        print(f"Error creating title clip for {input_file}: {e}")

# Input MP4 files and corresponding titles
video_files = ['pumpkin5.mp4', 'pumpkin6.mp4', 'pumpkin7.mp4', 'pumpkin89.mp4', 'pumpkin10.mp4']
titles = [
    'The Virus Made Animals Giant: My Friends and I ride them through the forest of death',  # Main title
    'Vines burst from the ground and grab the tortoise. Its shell glows blue. The girl commands her wolf to bite the vines while she cuts them with a dagger.',
    'Vines retreat. Mist clears. Giant blue butterflies emerge. The fluttering blue butterflies obstruct the foreground, they fly off. The girl leads her wolf deeper into the forest.',
    'A massive red centipede crawls out, the boy throws a Molotov cocktail from the tortoise shell, burning the centipede with an explosion. The centipede disappears. The girl on the wolf and the boy on the turtle escape deeper into the forest.',
    'They reach the forest exit — an open field with giant rabbits and antelopes under the sunset. The girl smiles toward the horizon.'
]

# Create title clips (main title uses first video's frame)
title_clips = [f"title_main.mp4"] + [f"title_{os.path.splitext(file)[0]}.mp4" for file in video_files]
for i, (input_file, output_file, title) in enumerate(zip(video_files, title_clips, titles)):
    create_title_clip(input_file, output_file, title, duration=3.0, pixelation_factor=0.1)

In [ ]:
# Install moviepy if not already installed
!pip install moviepy

from moviepy.editor import VideoFileClip, concatenate_videoclips
import numpy as np
import os

# Function to normalize audio volume
def normalize_audio(clip, target_dBFS=-20.0):
    if clip.audio is None:
        print(f"Warning: No audio in clip {clip.filename or 'unknown'}. Skipping normalization.")
        return clip
    try:
        # Get the audio as an array
        audio = clip.audio.to_soundarray()
        # Ensure audio is a 2D array (handles mono/stereo)
        if audio.ndim == 1:
            audio = audio[:, np.newaxis]
        # Calculate current dBFS
        current_dBFS = 10 * np.log10(np.mean(audio**2) + 1e-10)  # Avoid log(0)
        # Calculate gain needed to reach target dBFS
        gain = target_dBFS - current_dBFS
        # Apply gain to audio
        return clip.volumex(10 ** (gain / 20.0))
    except Exception as e:
        print(f"Error normalizing audio for clip {clip.filename or 'unknown'}: {e}. Skipping normalization.")
        return clip

# Input MP4 files and corresponding title clips
video_files = ['pumpkin5.mp4', 'pumpkin6.mp4', 'pumpkin7.mp4', 'pumpkin89.mp4', 'pumpkin10.mp4']
title_clips = [f"title_main.mp4"] + [f"title_{os.path.splitext(file)[0]}.mp4" for file in video_files]

# Load clips
clips = []
for i, (title_file, video_file) in enumerate(zip(title_clips, video_files)):
    try:
        # Check if files exist
        if not os.path.exists(title_file):
            print(f"Error: Title file {title_file} not found. Skipping this pair.")
            continue
        if not os.path.exists(video_file):
            print(f"Error: Video file {video_file} not found. Skipping this pair.")
            continue
        # Load title clip (no audio)
        title_clip = VideoFileClip(title_file)
        clips.append(title_clip)
        # Load and normalize original video
        video_clip = VideoFileClip(video_file)
        video_clip = normalize_audio(video_clip, target_dBFS=-20.0)
        clips.append(video_clip)
    except Exception as e:
        print(f"Error loading {title_file} or {video_file}: {e}. Skipping this pair.")
        continue

# Check if any clips were loaded
if not clips:
    raise ValueError("No valid clips were loaded. Please check your files.")

# Concatenate all clips (no fade transitions)
final_sequence = clips  # Sequence: title_main, pumpkin5, title_pumpkin6, pumpkin6, ...
final_video = concatenate_videoclips(final_sequence, method="compose")

# Ensure audio fades for the entire video
final_video = final_video.audio_fadein(1.24).audio_fadeout(1.24)

# Save the final video
output_path = "output_video.mp4"
try:
    final_video.write_videofile(output_path, codec="libx264", audio_codec="aac")
    print(f"Video saved as {output_path}")
except Exception as e:
    print(f"Error saving video: {e}")

# Close clips to free memory
for clip in clips:
    clip.close()
final_video.close()